# GTFS and AVL Summary Tables

In [ ]:
import pandas as pd
import os
import numpy as np
# Set the workspace environment to master folder
x=os.chdir('C:\\Users\\Cole\\Desktop\\Spring2022\\AVLResearch')

## GTFS - gives start/end time for each trip, each day (no bus info)

In [ ]:
#open the outputs from GTFS Joining(PANDAS)
calendar = pd.read_csv('Data\\GTFS_Query\\cal_select.txt', index_col = False)
routes = pd.read_csv('Data\\GTFS_Query\\routes_select.txt', index_col = False)
shapes = pd.read_csv('Data\\GTFS_Query\\shapes_select.txt', index_col = False)
stop_times= pd.read_csv('Data\\GTFS_Query\\stop_times_select.txt', index_col = False)
stops = pd.read_csv('Data\\GTFS_Query\\stops_select.txt', index_col = False)
trips = pd.read_csv('Data\\GTFS_Query\\trips_select.txt', index_col = False)

In [ ]:
#should give you stop times w/ stop locations for each trip
add_trip_stop_times = pd.merge(stop_times,trips,how = 'left', on = ['trip_id','route_id','service_id', 'trip_headsign','shape_id'])

In [ ]:
#error happens here? Fixed: left to outer join
add_trip_stops = pd.merge(add_trip_stop_times,stops, how = 'outer', on = ['stop_id'])
#add_trip_stops.to_csv(r"C:\Users\Cole\Desktop\Spring2022\AVLResearch\Data\ProcessedAVL_GTFS\Test.csv", index = False)

add_trip_stops = add_trip_stops.sort_values(by =['trip_id', 'stop_sequence_x'])
add_trip_stops.to_csv(r"C:\Users\Cole\Desktop\Spring2022\AVLResearch\Data\ProcessedAVL_GTFS\Test.csv", index = False)
add_trip_stops

In [ ]:
add_trip_stops['SERV_DAY'] = add_trip_stops['trip_id'].str[22:-3]
for index in range(len(add_trip_stops)):
    if 'Northbound' in add_trip_stops.loc[index,'trip_headsign']:
        add_trip_stops.loc[index,'dir_sign'] = 4
    if 'Southbound' in add_trip_stops.loc[index,'trip_headsign']:
        add_trip_stops.loc[index,'dir_sign'] = 1
GTFSSum = add_trip_stops.replace({np.nan: None})
#GTFSSum.to_csv(r"C:\Users\Cole\Desktop\Spring2022\AVLResearch\Data\ProcessedAVL_GTFS\Test.csv", index = False)

In [ ]:
groupedtrips = GTFSSum.groupby("trip_id",sort=True)
for group in groupedtrips:
    a = groupedtrips.head(1)
    b = groupedtrips.tail(1)

In [ ]:
final = pd.merge(a,b, on= 'trip_id',suffixes = ('_start','_end'))
sumtableGTFS = final[['trip_id',
                     'service_id_start',
                     'trip_headsign_start',
                      'dir_sign_start',
                      'SERV_DAY_start',
                     
                     'stop_lat_start',
                      'stop_lon_start',
                      'arrival_time_start',
                      'departure_time_start',
                     'stop_id_start',
                     'stop_name_start',
                     'stop_desc_start',
                     
                      'stop_lat_end',
                      'stop_lon_end',
                      'arrival_time_end',
                      'departure_time_end',
                     'stop_id_end',
                     'stop_name_end',
                     'stop_desc_end'
                     ]]
sumtableGTFS= sumtableGTFS.sort_values(['service_id_start', 'dir_sign_start','arrival_time_start'])
sumtableGTFS.to_csv(r"C:\Users\Cole\Desktop\Spring2022\AVLResearch\Data\ProcessedAVL_GTFS\GTFS_Trips.csv", index = False)
#nice, in service ID, direction, trio arrangement

## AVL - proof table

In [2]:
import pandas as pd
import numpy as np
from datetime import datetime, tzinfo
from dateutil import tz
import pytz
dataPath = "C:\\Users\Cole\Desktop\Spring2022\AVLResearch\Data\Aline-vehicle-messages-Oct1_Oct8_2016\Aline-vehicle-messages-Oct1_Oct8-2016.csv"
dataFrame = pd.read_csv(dataPath)
avl_messages = dataFrame[["CALENDAR_ID",
                          "MESSAGE_TIMESTAMP",
                          "LOCAL_TIMESTAMP",
                          "SOURCE_HOST",
                          "ROUTE_ABBR",
                          "DIRECTION",
                          "LONGITUDE",
                          "LATITUDE"]]
newframe = avl_messages.replace({np.nan: None})
newframe

CALENDAR_ID         MESSAGE_TIMESTAMP           LOCAL_TIMESTAMP  \
0         120161001  2016-10-01T10:40:28.110Z                      None   
1         120161001  2016-10-01T10:41:28.280Z                      None   
2         120161001  2016-10-01T10:42:28.277Z                      None   
3         120161001  2016-10-01T10:43:28.277Z                      None   
4         120161001  2016-10-01T10:44:28.273Z                      None   
...             ...                       ...                       ...   
126878    120161008  2016-10-09T11:31:07.047Z  2016-10-09T06:07:03.053Z   
126879    120161008  2016-10-09T11:31:08.840Z  2016-10-09T06:07:03.053Z   
126880    120161008  2016-10-09T11:31:19.073Z  2016-10-09T06:07:03.053Z   
126881    120161008  2016-10-09T11:32:19.087Z  2016-10-09T06:07:03.053Z   
126882    120161008  2016-10-09T11:33:19.070Z  2016-10-09T06:07:03.053Z   

        SOURCE_HOST ROUTE_ABBR DIRECTION  LONGITUDE   LATITUDE  
0              2640       None      None -932434771  448637316  
1              2640       None      None -932444569  448627351  
2              2640       None      None -932439966  448632202  
3              2640       None      None -932439023  448632056  
4              2640       None      None -932441450  448631769  
...             ...        ...       ...        ...        ...  
126878         2643      921.0       4.0 -932440665  448632444  
126879         2643      921.0       4.0 -932440539  448632524  
126880         2643      921.0       4.0 -932441667  448629753  
126881         2643      921.0       4.0 -932440018  448629602  
126882         2643      921.0       4.0 -932439624  448627871  

[126883 rows x 8 columns]

In [3]:
#Fix local_time for each row in AVL full data 
for index in range(len(newframe)):
    try:
        dt_str = newframe.loc[index, 'LOCAL_TIMESTAMP']
        dt_str1 = dt_str.replace('T',"").replace('Z',"")
        t3 = datetime.strptime(dt_str1,"%Y-%m-%d%H:%M:%S.%f")
        newframe.loc[index,'TIME'] = t3
    except:
        pass

Local timestamp is not as specific as message timestamp;
several messages in a row are given the same time.
But say we remove any duplicates,
so there is just one of each local timestamp time for simplicity 

In [4]:
#will eventually drop this cell
#works for both versions
newframe = newframe.drop_duplicates(subset = ['TIME'], keep = 'last')

In [5]:
#sorts by bus # and then stripped LOCAL_TIME or ('TIME')
time_sorted = newframe.sort_values(["SOURCE_HOST",
                                        'TIME'],
                                       axis=0,
                                       ascending=(True, True))

In [6]:
#group by source host (keeps them in time order) and reset index
groupedhost = time_sorted.groupby('SOURCE_HOST')
time_sorted.reset_index(drop=True)

#Mark rows where the day ends and new day begins
time_sorted['PREVDAY'] = groupedhost.transform(lambda x: x.shift(-1) > x+pd.Timedelta('1h'))
time_sorted['NEXTDAY'] = time_sorted['PREVDAY'].shift(1)
time_sorted.reset_index(drop = True)

C:\Users\Cole\Anaconda3\lib\site-packages\ipykernel_launcher.py:6: FutureWarning: Dropping invalid columns in DataFrameGroupBy.transform is deprecated. In a future version, a TypeError will be raised. Before calling .transform, select only columns which should be valid for the transforming function.
  


CALENDAR_ID         MESSAGE_TIMESTAMP           LOCAL_TIMESTAMP  \
0        120161001  2016-10-01T14:00:50.890Z  2016-10-01T09:00:50.890Z   
1        120161001  2016-10-01T14:36:04.203Z  2016-10-01T09:02:00.373Z   
2        120161001  2016-10-01T14:40:09.407Z  2016-10-01T09:37:08.197Z   
3        120161001  2016-10-01T14:40:17.207Z  2016-10-01T09:40:17.207Z   
4        120161001  2016-10-01T14:40:53.803Z  2016-10-01T09:40:21.997Z   
...            ...                       ...                       ...   
20119    120161007  2016-10-08T04:03:37.127Z  2016-10-07T23:03:32.447Z   
20120    120161007  2016-10-08T04:09:51.063Z  2016-10-07T23:05:18.193Z   
20121    120161007  2016-10-08T04:10:39.690Z  2016-10-07T23:10:39.690Z   
20122    120161007  2016-10-08T04:24:48.040Z  2016-10-07T23:10:44.900Z   
20123    120161007  2016-10-08T05:41:30.190Z  2016-10-07T23:25:00.053Z   

       SOURCE_HOST ROUTE_ABBR DIRECTION  LONGITUDE   LATITUDE  \
0             2639      921.0       1.0 -932437104  448629658   
1             2639      921.0       1.0 -931685283  450125767   
2             2639      921.0       1.0 -931668135  449912112   
3             2639      921.0       1.0 -931667658  449908048   
4             2639      921.0       1.0 -931670992  449874601   
...            ...        ...       ...        ...        ...   
20119         2651      921.0       1.0 -931942988  449179172   
20120         2651      921.0       1.0 -932203832  449210893   
20121         2651      921.0       1.0 -932208611  449209546   
20122         2651      921.0       1.0 -932422746  448632047   
20123         2651      921.0       1.0 -932424522  448641748   

                         TIME  PREVDAY NEXTDAY  
0     2016-10-01 09:00:50.890    False     NaN  
1     2016-10-01 09:02:00.373    False   False  
2     2016-10-01 09:37:08.197    False   False  
3     2016-10-01 09:40:17.207    False   False  
4     2016-10-01 09:40:21.997    False   False  
...                       ...      ...     ...  
20119 2016-10-07 23:03:32.447    False   False  
20120 2016-10-07 23:05:18.193    False   False  
20121 2016-10-07 23:10:39.690    False   False  
20122 2016-10-07 23:10:44.900    False   False  
20123 2016-10-07 23:25:00.053    False   False  

[20124 rows x 11 columns]

In [8]:
#Select rows with marks, put them together, final sort, export
final = time_sorted.loc[time_sorted['PREVDAY'] == True] 
final2 = time_sorted.loc[time_sorted['NEXTDAY'] == True]
x = pd.concat([final,final2])
y = x.sort_values(["SOURCE_HOST",'TIME'],axis=0,ascending=(True, True))
y.to_csv(r"C:\Users\Cole\Desktop\Spring2022\AVLResearch\Data\ProcessedAVL_GTFS\AVL_StartStop_ofDay_EachBus.csv",  index=False)

AVL: Grouped by bus, then time, then takes first and last time for each service day <br>
GTFS: Sorted by service day, then direction, assign trip numbers (+1 when direction change, reset at day change), start/stop each trip *Good to go*

So we'll still need an AVL that is service_day, then time, assign trip numbers (+1 when direction change, reset at day change). For each day, line up GTFS and AVL against each other to compare

# AVL Trips (to match GTFS)

In [21]:
import pandas as pd
import numpy as np
from datetime import datetime, tzinfo
from dateutil import tz
import pytz
dataPath = "C:\\Users\Cole\Desktop\Spring2022\AVLResearch\Data\Aline-vehicle-messages-Oct1_Oct8_2016\Aline-vehicle-messages-Oct1_Oct8-2016.csv"
dataFrame = pd.read_csv(dataPath)
avl_messages = dataFrame[["CALENDAR_ID",
                          "MESSAGE_TIMESTAMP",
                          "LOCAL_TIMESTAMP",
                          "SOURCE_HOST",
                          "ROUTE_ABBR",
                          "DIRECTION",
                          "LONGITUDE",
                          "LATITUDE"]]
newframe = avl_messages.replace({np.nan: None})

In [22]:
#Fix local_time for each row in AVL full data 
for index in range(len(newframe)):
    try:
        dt_str = newframe.loc[index, 'MESSAGE_TIMESTAMP']
        dt_str1 = dt_str.replace('T',"").replace('Z',"")
        dt_utc = datetime.strptime(dt_str1,"%Y-%m-%d%H:%M:%S.%f")
        dt_utc = dt_utc.replace(tzinfo = pytz.UTC)
        local_zone = tz.tzlocal()
        dt_local = dt_utc.astimezone(local_zone)
        local_time_str = dt_local.strftime("%Y-%m-%d%H:%M:%S.%f")
        print(local_time_str)
        
        
        
        newframe.loc[index,'TIME'] = local_time_str
    except:
        pass

2016-10-0105:40:28.110000
2016-10-0105:41:28.280000
2016-10-0105:42:28.277000
2016-10-0105:43:28.277000
2016-10-0105:44:28.273000
2016-10-0105:45:28.367000
2016-10-0105:46:28.270000
2016-10-0105:47:28.283000
2016-10-0105:48:28.283000
2016-10-0105:49:28.280000
2016-10-0105:50:28.277000
2016-10-0105:51:28.290000
2016-10-0105:52:28.273000
2016-10-0105:53:28.287000
2016-10-0105:54:28.287000
2016-10-0105:55:28.283000
2016-10-0105:56:28.280000
2016-10-0105:57:28.280000
2016-10-0105:58:28.293000
2016-10-0106:00:28.290000
2016-10-0106:01:28.287000
2016-10-0106:03:28.283000
2016-10-0106:04:28.280000
2016-10-0106:05:28.277000
2016-10-0106:06:28.277000
2016-10-0106:08:28.287000
2016-10-0106:09:28.317000
2016-10-0106:10:28.283000
2016-10-0106:11:28.283000
2016-10-0106:12:28.280000
2016-10-0106:13:28.277000
2016-10-0106:14:28.293000
2016-10-0106:15:28.320000
2016-10-0106:40:36.397000
2016-10-0106:41:36.880000
2016-10-0106:42:36.877000
2016-10-0106:43:36.877000
2016-10-0106:44:36.907000
2016-10-0106

2016-10-0109:04:38.527000
2016-10-0109:04:43.923000
2016-10-0109:04:45.343000
2016-10-0109:05:05.780000
2016-10-0109:05:45.730000
2016-10-0109:06:05.777000
2016-10-0109:06:45.730000
2016-10-0109:07:05.777000
2016-10-0109:07:45.727000
2016-10-0109:08:05.773000
2016-10-0109:09:05.770000
2016-10-0109:09:39.733000
2016-10-0109:09:41.137000
2016-10-0109:10:05.787000
2016-10-0109:10:41.727000
2016-10-0109:11:05.797000
2016-10-0109:11:41.740000
2016-10-0109:12:05.780000
2016-10-0109:12:41.740000
2016-10-0109:12:54.127000
2016-10-0109:12:55.530000
2016-10-0109:13:05.780000
2016-10-0109:13:55.933000
2016-10-0109:14:05.777000
2016-10-0109:14:55.930000
2016-10-0109:15:05.777000
2016-10-0109:15:55.930000
2016-10-0109:16:05.787000
2016-10-0109:16:55.927000
2016-10-0109:17:05.787000
2016-10-0109:18:05.783000
2016-10-0109:18:27.937000
2016-10-0109:18:29.137000
2016-10-0109:19:05.783000
2016-10-0109:19:29.527000
2016-10-0109:20:05.780000
2016-10-0109:21:05.777000
2016-10-0109:21:29.537000
2016-10-0109

2016-10-0110:35:18.437000
2016-10-0110:35:22.243000
2016-10-0110:35:38.047000
2016-10-0110:35:39.153000
2016-10-0110:35:52.350000
2016-10-0110:36:14.847000
2016-10-0110:36:22.460000
2016-10-0110:36:39.183000
2016-10-0110:36:42.757000
2016-10-0110:37:12.567000
2016-10-0110:37:14.847000
2016-10-0110:37:39.260000
2016-10-0110:38:12.987000
2016-10-0110:38:14.843000
2016-10-0110:38:38.243000
2016-10-0110:38:39.180000
2016-10-0110:38:42.097000
2016-10-0110:38:53.843000
2016-10-0110:39:00.147000
2016-10-0110:39:01.347000
2016-10-0110:39:14.840000
2016-10-0110:39:39.193000
2016-10-0110:39:42.437000
2016-10-0110:39:46.040000
2016-10-0110:40:01.390000
2016-10-0110:40:14.840000
2016-10-0110:40:39.190000
2016-10-0110:41:01.357000
2016-10-0110:41:07.957000
2016-10-0110:41:14.837000
2016-10-0110:42:01.357000
2016-10-0110:42:07.957000
2016-10-0110:42:14.850000
2016-10-0110:42:28.267000
2016-10-0110:42:31.137000
2016-10-0110:42:33.647000
2016-10-0110:43:01.353000
2016-10-0110:43:07.953000
2016-10-0110

2016-10-0111:44:24.693000
2016-10-0111:44:29.407000
2016-10-0111:44:32.573000
2016-10-0111:44:32.883000
2016-10-0111:44:38.343000
2016-10-0111:44:41.213000
2016-10-0111:44:42.417000
2016-10-0111:45:00.310000
2016-10-0111:45:05.113000
2016-10-0111:45:06.893000
2016-10-0111:45:12.413000
2016-10-0111:45:32.883000
2016-10-0111:45:38.187000
2016-10-0111:45:38.700000
2016-10-0111:45:57.483000
2016-10-0111:46:00.307000
2016-10-0111:46:02.490000
2016-10-0111:46:04.300000
2016-10-0111:46:05.830000
2016-10-0111:46:06.767000
2016-10-0111:46:13.177000
2016-10-0111:46:18.123000
2016-10-0111:46:38.183000
2016-10-0111:46:43.300000
2016-10-0111:46:52.507000
2016-10-0111:46:54.003000
2016-10-0111:47:00.307000
2016-10-0111:47:05.797000
2016-10-0111:47:06.780000
2016-10-0111:47:13.223000
2016-10-0111:47:37.963000
2016-10-0111:47:57.107000
2016-10-0111:48:00.303000
2016-10-0111:48:06.777000
2016-10-0111:48:10.037000
2016-10-0111:48:10.897000
2016-10-0111:48:13.033000
2016-10-0111:48:14.810000
2016-10-0111

2016-10-0112:25:14.507000
2016-10-0112:25:15.723000
2016-10-0112:25:34.690000
2016-10-0112:25:37.887000
2016-10-0112:25:46.197000
2016-10-0112:25:59.330000
2016-10-0112:26:04.070000
2016-10-0112:26:05.287000
2016-10-0112:26:34.667000
2016-10-0112:26:37.877000
2016-10-0112:26:38.860000
2016-10-0112:26:47.097000
2016-10-0112:26:52.663000
2016-10-0112:26:59.257000
2016-10-0112:27:02.220000
2016-10-0112:27:04.123000
2016-10-0112:27:08.117000
2016-10-0112:27:30.667000
2016-10-0112:27:37.947000
2016-10-0112:27:38.837000
2016-10-0112:27:46.823000
2016-10-0112:27:59.283000
2016-10-0112:28:03.383000
2016-10-0112:28:04.227000
2016-10-0112:28:06.207000
2016-10-0112:28:19.960000
2016-10-0112:28:21.037000
2016-10-0112:28:32.997000
2016-10-0112:28:37.830000
2016-10-0112:28:38.830000
2016-10-0112:28:46.610000
2016-10-0112:28:55.827000
2016-10-0112:28:59.210000
2016-10-0112:29:04.123000
2016-10-0112:29:08.660000
2016-10-0112:29:21.620000
2016-10-0112:29:37.807000
2016-10-0112:29:38.790000
2016-10-0112

...

2016-10-0902:15:04.437000
2016-10-0902:15:23.263000
2016-10-0902:15:25.620000
2016-10-0902:15:40.050000
2016-10-0902:15:51.437000
2016-10-0902:15:55.417000
2016-10-0902:15:57.803000
2016-10-0902:15:58.410000
2016-10-0902:16:02.420000
2016-10-0902:16:04.433000
2016-10-0902:16:07.210000
2016-10-0902:16:10.237000
2016-10-0902:16:11.843000
2016-10-0902:16:16.553000
2016-10-0902:16:19.020000
2016-10-0902:16:20.237000
2016-10-0902:16:22.827000
2016-10-0902:16:23.620000
2016-10-0902:16:37.240000
2016-10-0902:16:38.440000
2016-10-0902:16:51.343000
2016-10-0902:16:57.833000
2016-10-0902:16:58.410000
2016-10-0902:17:12.840000
2016-10-0902:17:13.837000
2016-10-0902:17:20.750000
2016-10-0902:17:23.057000
2016-10-0902:17:34.243000
2016-10-0902:17:38.847000
2016-10-0902:17:51.230000
2016-10-0902:17:57.817000
2016-10-0902:17:58.440000
2016-10-0902:18:14.007000
2016-10-0902:18:16.410000
2016-10-0902:18:20.013000
2016-10-0902:18:20.030000
2016-10-0902:18:20.827000
2016-10-0902:18:25.753000
2016-10-0902

2016-10-0902:47:09.513000
2016-10-0902:47:10.107000
2016-10-0902:47:18.390000
2016-10-0902:47:27.997000
2016-10-0902:47:50.790000
2016-10-0902:47:53.397000
2016-10-0902:48:06.687000
2016-10-0902:48:09.633000
2016-10-0902:48:11.193000
2016-10-0902:48:17.183000
2016-10-0902:48:18.387000
2016-10-0902:48:23.783000
2016-10-0902:48:25.593000
2016-10-0902:48:34.203000
2016-10-0902:48:35.797000
2016-10-0902:48:41.193000
2016-10-0902:48:46.590000
2016-10-0902:48:50.787000
2016-10-0902:48:51.397000
2016-10-0902:48:53.453000
2016-10-0902:48:55.203000
2016-10-0902:49:07.197000
2016-10-0902:49:09.553000
2016-10-0902:49:17.400000
2016-10-0902:49:29.397000
2016-10-0902:49:33.857000
2016-10-0902:49:41.207000
2016-10-0902:49:50.830000
2016-10-0902:49:53.437000
2016-10-0902:50:07.103000
2016-10-0902:50:09.537000
2016-10-0902:50:20.907000
2016-10-0902:50:24.620000
2016-10-0902:50:36.820000
2016-10-0902:50:44.027000
2016-10-0902:50:46.210000
2016-10-0902:50:50.797000
2016-10-0902:50:53.467000
2016-10-0902

2016-10-0903:23:25.597000
2016-10-0903:23:30.683000
2016-10-0903:23:32.807000
2016-10-0903:23:37.423000
2016-10-0903:23:37.643000
2016-10-0903:23:49.013000
2016-10-0903:23:52.213000
2016-10-0903:23:57.610000
2016-10-0903:24:00.997000
2016-10-0903:24:05.817000
2016-10-0903:24:36.017000
2016-10-0903:24:39.620000
2016-10-0903:24:40.823000
2016-10-0903:24:43.023000
2016-10-0903:24:52.210000
2016-10-0903:25:04.597000
2016-10-0903:25:05.847000
2016-10-0903:25:08.200000
2016-10-0903:25:23.427000
2016-10-0903:25:41.037000
2016-10-0903:25:45.017000
2016-10-0903:25:48.417000
2016-10-0903:25:52.257000
2016-10-0903:26:01.227000
2016-10-0903:26:05.810000
2016-10-0903:26:11.083000
2016-10-0903:26:13.813000
2016-10-0903:26:15.017000
2016-10-0903:26:21.630000
2016-10-0903:26:23.813000
2016-10-0903:26:32.427000
2016-10-0903:26:48.417000
2016-10-0903:26:50.817000
2016-10-0903:26:55.827000
2016-10-0903:26:59.430000
2016-10-0903:27:05.810000
2016-10-0903:27:06.043000
2016-10-0903:27:11.190000
2016-10-0903

2016-10-0904:10:15.410000
2016-10-0904:10:17.237000
2016-10-0904:10:20.467000
2016-10-0904:10:25.050000
2016-10-0904:10:36.657000
2016-10-0904:10:40.247000
2016-10-0904:10:47.360000
2016-10-0904:10:48.450000
2016-10-0904:10:49.857000
2016-10-0904:11:15.423000
2016-10-0904:11:25.050000
2016-10-0904:11:44.503000
2016-10-0904:11:48.043000
2016-10-0904:11:48.467000
2016-10-0904:11:50.463000
2016-10-0904:12:15.407000
2016-10-0904:12:20.430000
2016-10-0904:12:25.047000
2016-10-0904:12:48.447000
2016-10-0904:12:50.443000
2016-10-0904:12:51.303000
2016-10-0904:13:15.403000
2016-10-0904:13:20.443000
2016-10-0904:13:25.047000
2016-10-0904:13:48.447000
2016-10-0904:13:50.457000
2016-10-0904:13:55.043000
2016-10-0904:13:58.867000
2016-10-0904:14:15.403000
2016-10-0904:14:20.457000
2016-10-0904:14:25.043000
2016-10-0904:14:48.443000
2016-10-0904:14:50.457000
2016-10-0904:14:57.273000
2016-10-0904:14:59.037000
2016-10-0904:15:15.027000
2016-10-0904:15:15.417000
2016-10-0904:15:24.027000
2016-10-0904

2016-10-0905:00:38.290000
2016-10-0905:00:56.370000
2016-10-0905:01:03.670000
2016-10-0905:01:12.047000
2016-10-0905:01:42.093000
2016-10-0905:01:48.160000
2016-10-0905:01:56.290000
2016-10-0905:02:16.147000
2016-10-0905:02:19.847000
2016-10-0905:02:48.487000
2016-10-0905:02:53.823000
2016-10-0905:02:56.287000
2016-10-0905:03:03.637000
2016-10-0905:03:15.023000
2016-10-0905:03:19.827000
2016-10-0905:03:24.413000
2016-10-0905:03:51.107000
2016-10-0905:03:56.287000
2016-10-0905:04:54.100000
2016-10-0905:04:56.283000
2016-10-0905:04:58.077000
2016-10-0905:05:01.727000
2016-10-0905:05:30.620000
2016-10-0905:05:49.620000
2016-10-0905:05:56.280000
2016-10-0905:06:00.243000
2016-10-0905:06:01.680000
2016-10-0905:06:56.280000
2016-10-0905:07:04.017000
2016-10-0905:07:04.080000
2016-10-0905:07:07.620000
2016-10-0905:07:32.223000
2016-10-0905:07:40.473000
2016-10-0905:07:56.277000
2016-10-0905:08:04.093000
2016-10-0905:08:33.857000
2016-10-0905:08:38.227000
2016-10-0905:08:48.070000
2016-10-0905

In [ ]:
#something like give value until >3 hr time gap, then add one